## Binary search

* This example builds on the tidied [Urban Audit dataset on countries](./data/urb_cpop1_countries_tidy.csv).
* It is based on the Python recipes available from: http://python3.codes/binary-search/

The search task is:
* Find the population per country for a given year (e.g., 2010)
* Find a country having more than 5m inhabitants that year.

In [14]:
import pandas as pd
import numpy as np

import os.path

urbanAuditFile = './data/urb_cpop1_countries_tidy.csv'
df_ua = pd.read_csv(urbanAuditFile, index_col = 0, na_values = ':') # this turns ':' into NaN
df_ua['population'] = df_ua['population'].str.replace(" ","").fillna(-1).astype(int).replace(-1, np.nan)
# df_ua.sample(10)
df_ua_2010 = df_ua[(df_ua['year'] == 2010) & (df_ua['indic_ur'] == 'DE1001V')]
df_ua_2010

entity indic_ur  year  population
20      BE  DE1001V  2010  10839905.0
47      BG  DE1001V  2010   7563710.0
74      CZ  DE1001V  2010  10532770.0
101     DK  DE1001V  2010         NaN
128     DE  DE1001V  2010  81802257.0
155     EE  DE1001V  2010   1365275.0
182     IE  DE1001V  2010         NaN
209     EL  DE1001V  2010         NaN
236     ES  DE1001V  2010  47021031.0
263     FR  DE1001V  2010  64611814.0
290     IT  DE1001V  2010  60340328.0
317     CY  DE1001V  2010    819100.0
344     LV  DE1001V  2010         NaN
371     LT  DE1001V  2010         NaN
398     LU  DE1001V  2010         NaN
425     HU  DE1001V  2010  10014324.0
452     MT  DE1001V  2010         NaN
479     NL  DE1001V  2010  16574989.0
506     AT  DE1001V  2010         NaN
533     PL  DE1001V  2010  38529866.0
560     PT  DE1001V  2010  10573479.0
587     RO  DE1001V  2010  22480599.0
614     SI  DE1001V  2010         NaN
641     SK  DE1001V  2010   5435273.0
668     FI  DE1001V  2010   5351427.0
695     SE  DE1001V  2010   9415570.0
722     UK  DE1001V  2010         NaN
749     TR  DE1001V  2010         NaN
776     NO  DE1001V  2010   4858199.0
803     CH  DE1001V  2010   7877571.0

In [64]:
# drop the missings (NaN) and turn into int
df_ua_2010 = df_ua_2010.dropna().copy()
df_ua_2010['population'] = df_ua_2010['population'].astype(int)
n = df_ua_2010.shape[0]
n

haystack = [(df_ua_2010['population'].tolist()[i], df_ua_2010['entity'].tolist()[i]) for i in range(0,n)]
haystack


[(10839905, 'BE'),
 (7563710, 'BG'),
 (10532770, 'CZ'),
 (81802257, 'DE'),
 (1365275, 'EE'),
 (47021031, 'ES'),
 (64611814, 'FR'),
 (60340328, 'IT'),
 (819100, 'CY'),
 (10014324, 'HU'),
 (16574989, 'NL'),
 (38529866, 'PL'),
 (10573479, 'PT'),
 (22480599, 'RO'),
 (5435273, 'SK'),
 (5351427, 'FI'),
 (9415570, 'SE'),
 (4858199, 'NO'),
 (7877571, 'CH')]

In [66]:
haystack.sort() # by country code
haystack.sort(key=lambda x:x[0]) # by population count

haystack

[(819100, 'CY'),
 (1365275, 'EE'),
 (4858199, 'NO'),
 (5351427, 'FI'),
 (5435273, 'SK'),
 (7563710, 'BG'),
 (7877571, 'CH'),
 (9415570, 'SE'),
 (10014324, 'HU'),
 (10532770, 'CZ'),
 (10573479, 'PT'),
 (10839905, 'BE'),
 (16574989, 'NL'),
 (22480599, 'RO'),
 (38529866, 'PL'),
 (47021031, 'ES'),
 (60340328, 'IT'),
 (64611814, 'FR'),
 (81802257, 'DE')]

A naive sort requires $(n^2-n)/2)$ comparisons (in the worst case!), which yields a time-growth rate at the order of $O(n^2)$

In [67]:
(n**2-n)/2
# i.e.
n**2

361

Python's `sort` yields a growth rate of $O(n\log{}n)$:

In [68]:
n * np.log(n)

55.944340604162363

Can we do better? Maybe $O(\log{}n)$?

1. Sort according to population count (ideally, make sure that the data is already inserted in a sorted manner!)
2. Run a binary search: Find one country having more than 5m inhabitants!

In [88]:
def binary_search(number, array, lo, hi):

    if hi < lo: return array[lo]       # no more numbers
    mid = (lo + hi) // 2               # midpoint in array
    if number == array[mid][0]:
        return array[mid]              # number found here
    elif number < array[mid][0]:
        # try left of here
        return binary_search(number, array, lo, mid - 1)
    else:
        # try above here
        return binary_search(number, array, mid + 1, hi)

binary_search(5000000, haystack, 0, len(haystack))

(5351427, 'FI')

* Question: Find one country having more than 5m inhabitants!
* Answer: FI for Finland with 5351427 inhabitants (2010)